In [111]:
import geopandas as gpd
import matplotlib.pyplot as plt
import numpy as np

In [112]:
octo = gpd.read_file('/Users/gr_1/Documents/cosmo_predict/octo_327_data')
octo.index = range(len(octo))

## a note

In [ ]:
fig,ax = plt.subplots(figsize = (20,10))
world = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))
world.plot(ax=ax,color='gray')
a = octo.plot(ax=ax,column='ebe_mmkyr',cmap='jet',legend=True,vmax=100)

In [ ]:
import pandas as pd
import folium
from folium.plugins import FastMarkerCluster

df = octo.copy()
df.geometry = octo.geometry.centroid
df['lon'] = df.geometry.x
df['lat'] = df.geometry.y


folium_map = folium.Map(
                        tiles='CartoDB dark_matter')

# These two lines should create FastMarkerClusters
FastMarkerCluster(data=list(zip(df['lat'].values, df['lon'].values))).add_to(folium_map)
folium.LayerControl().add_to(folium_map)

for index, row in df.iterrows():

    popup_text = "{}<br> erosion rate: {:,}<br> avg slope: {:,}"
    popup_text = popup_text.format(
                      index,
                      row["ebe_mmkyr"],
                      row["slp_ave"]
                      )

    folium.CircleMarker(location=(row["lat"],
                                  row["lon"]),
                        color=,
                        popup=popup_text,
                        fill=False).add_to(folium_map)
folium_map

In [118]:
folium_map.save('/Users/gr_1/Desktop/fomap.html')

In [116]:
import altair as alt

source = df

scale = alt.Scale(domain=['sun', 'fog', 'drizzle', 'rain', 'snow'],
                  range=['#e7ba52', '#a7a7a7', '#aec7e8', '#1f77b4', '#9467bd'])
color = alt.Color('ebe_mmkyr:Q', scale=scale)

# We create two selections:
# - a brush that is active on the top panel
# - a multi-click that is active on the bottom panel
brush = alt.selection_interval(encodings=['x','y'])
click = alt.selection_multi(encodings=['color'])

# Top panel is scatter plot of temperature vs time
points = alt.Chart().mark_point().encode(
    alt.X('lon:Q', title='LON'),
    alt.Y('lat:Q',
        title='LON',
    ),
    color=alt.condition(brush, color, alt.value('lightgray')),
).properties(
    width=550,
    height=300
).add_selection(
    brush
).transform_filter(
    click
)

# Bottom panel is a bar chart of weather type
bars = alt.Chart().mark_bar().encode(
    x='count()',
    y=alt.Y('ebe_mmkyr:Q',bin=True),
    color=alt.condition(click, color, alt.value('lightgray')),
).transform_filter(
    brush
).properties(
    width=550,
).add_selection(
    click
)

a = alt.vconcat(
    points,
    bars,
    data=source,
    title="Octopus data"
)
a

alt.VConcatChart(...)